In [1]:
import branca
import geopandas
import folium
import pandas as pd

def heatmap(series, geodata, location, fields, aliases, caption,
            colors=['white','yellow','orange','red','darkred']):

    min_cn, max_cn = series[fields[0]].quantile([0.01,0.99]).apply(round, 2)
    colormap = branca.colormap.LinearColormap(
        colors=colors,
        vmin=min_cn,
        vmax=max_cn
    )

    colormap.caption=caption

    geodata = geodata.join(series.set_index("comuna"), how = "left", on = "NOMBRE")
    geodata.fillna(0, inplace = True)

    m = folium.Map(location=location,
                            zoom_start=12,
                            tiles="OpenStreetMap")
    style_function = lambda x: {
        'fillColor': colormap(x['properties'][fields[0]]),
        'color': 'black',
        'weight':2,
        'fillOpacity':0.6
    }

    stategeo = folium.GeoJson(
        geodata,
        name='Teaté Stores',
        style_function=style_function,
        tooltip=folium.GeoJsonTooltip(
            fields=['NOMBRE']+fields,
            aliases=['Comuna']+aliases, 
            localize=True
        )
    ).add_to(m)

    colormap.add_to(m)
    return m

def df_to_geojson(df, properties, lat='latitud', lon='longitud'):
    df=df.dropna(subset=[lat, lon])
    geojson = {'type':'FeatureCollection', 'features':[]}
    for _, row in df.iterrows():
        try:
            feature = {'type':'Feature',
                       'properties':{},
                       'geometry':{'type':'Point',
                                   'coordinates':[]}}
            feature['geometry']['coordinates'] = [row[lon],row[lat]]
            for prop in properties:
                feature['properties'][prop] = row[prop]
            geojson['features'].append(feature)
        except:
            pass
    return geojson

def point_map(series, location, fields, aliases):
    geodata = df_to_geojson(series, fields)
    m = folium.Map(location=location,
                   zoom_start=12,
                   tiles="OpenStreetMap")
    stategeo = folium.GeoJson(geodata, 
                   name='Teaté Stores', 
                   tooltip=folium.features.GeoJsonTooltip(fields=fields,
                                                          aliases=aliases,
                                                          localize=True)
                  ).add_to(m)

    return m

In [2]:
from sqlalchemy import *
import pandas as pd
user_name='postgres'
password='12345678'
host='teate.ctslcs9kjcvo.us-east-2.rds.amazonaws.com'
db_name='postgres'

connection_string=f"postgresql://{user_name}:{password}@{host}/{db_name}"
engine = create_engine(connection_string, max_overflow=20)

def run_query(sql,engine):
    result = engine.connect().execution_options(isolation_level="AUTOCOMMIT").execute((text(sql)))
    return pd.DataFrame(result.fetchall(), columns=result.keys())

In [3]:
citylocation = {'Bogota': [4.6097100, -74.0817500],
            'Medellin':[6.27162785, -75.60281325266426],
            'Cali': [3.4517923, -76.5324943]}

fields   = ["stores_count"]
aliases  = ["Total stores"]
caption  = "Total Number of Teate Stores by location"

In [4]:
centro = 3000
query = f"""SELECT COMUNA, COUNT(COMUNA) AS stores_count FROM TIENDAS
        WHERE CENTRO={centro}
        GROUP BY COMUNA """
series = run_query(query, engine)
series["comuna"]=series["comuna"].str.upper()
geodata  = geopandas.read_file("geojson_data/Comunas_Medellin.geojson", driver = "GeoJSON")
location = citylocation["Medellin"]
heatmap(series, geodata, location, fields, aliases, caption)

In [5]:
query = f"""SELECT * FROM TIENDAS
        WHERE CENTRO={centro} """
series = run_query(query, engine)
fields = ['nombre_tienda', 'cod_tienda', 'nombre_tendero']
aliases = ['Nombre de Tienda', 'Código', 'Nombre del Tendero']
location = citylocation["Medellin"]
m = point_map(series, location, fields, aliases)
m